In [99]:
import cv2 as cv
import numpy as np 
from enum import Enum


In [100]:
#calculate integralimage
def integral_image(img_arr):
    row_sum = np.zeros((img_arr.shape[0],img_arr.shape[1]))
    integral_image_arr = np.zeros((img_arr.shape[0] + 1, img_arr.shape[1] + 1))
    for x in range(img_arr.shape[1]):
        for y in range(img_arr.shape[0]):
            row_sum[y, x] = row_sum[y-1, x] + img_arr[y, x]
            integral_image_arr[y+1, x+1] = integral_image_arr[y+1, x-1+1] + row_sum[y, x]
            
    return integral_image_arr[1:integral_image_arr.shape[0],1:integral_image_arr.shape[1]]


In [101]:
#compute region
def compute_region(integral_image,topLeft,bottomRight):
    topLeft=(topLeft[1],topLeft[0])
    bottomRight=(bottomRight[1],bottomRight[0])
    if(topLeft==bottomRight):
        return integral_image[topLeft]
    else:
        topRight=(bottomRight[0],topLeft[1])
        botomLeft=(topLeft[0],bottomRight[1])
        sumRegion=(integral_image[bottomRight]+integral_image[topLeft])-(integral_image[bottomLeft]+integral_image[topRight])
        return sumRegion
    
     

In [102]:
#test integral image
x=np.array([[4,1,2,2],[0,4,1,3],[3,1,0,4],[2,1,3,2]])
y=integral_image(x)
print(y)

[[ 4.  5.  7.  9.]
 [ 4.  9. 12. 17.]
 [ 7. 13. 16. 25.]
 [ 9. 16. 22. 33.]]


In [103]:
#Haar Likes Features

class HaarFeaturesType(Enum):
    twoHorizontal=(2,1)
    twoVertical=(1,2)
    threeHorizontal=(3,1)
    threeVertical=(1,3)
    four=(2,2)
 


In [104]:
class HaarLikesFeatures(object):
    def __init__(self,featurType,position,width,height,threshold,parity,weight=1):
        self.type=featurType
        self.topLeft=position
        self.width=width
        self.height=height
        self.threshold=threshold
        self.parity=parity
        self.bottomRight=(position[0]+width,position[1]+height)
        self.weight=weight
        def calc_score(self,integral_image):
            
            white=0
            black=0
            if (self.type==HaarFeaturesType.twoHorizontal):
                white=compute_region(integral_image,self.topLeft,(int(self.topLeft[0]+self.width/2),int(self.topLeft[1]+self.height)))
                black= compute_region(integral_image,(int(self.topLeft[0]+self.width/2),self.topLeft[1]),self.bottomRight)
                
            elif(self.type==HaarFeaturesType.twoVertical):
                white=compute_region(integral_image,self.topLeft,(int(self.topLeft[0]+self.width),int(self.topLeft[1] + self.height / 2)))
                black=compute_region(integral_image,(self.topLeft[0],int(self.topLeft[1]+self.height/2)),self.bottomRight)
            elif(self.type==HaarFeaturesType. threeHorizontal):
                white=compute_region(integral_image,self.topLeft,(self.bottomRight[0],int(self.topLeft[1]+self.height/3)))
                black=compute_region(integral_image,(self.topLeft[0],int(self.TopLeft[1]+self.height/3)),(self.bottomRight[0],int(self.topLeft[1]+2*self.height/3)))
                white+=compute_region(integral_image,(self.topLeft[0],int(self.topLeft[1]+2*self.height/3)),self.bottomRight)
            elif(self.type==HaarFeaturesType.threeVertical):
                white=compute_region(integral_image,self.topLeft,(self.bottomRight[0],int(self.topLeft[1]+self.height/3)))
                black=compute_region(integral_image,(self.topLeft[0],int(self.topLeft[1]+self.height/3)),(self.bottomRight[0],int(self.topLeft[1]+2*self.height/3)))
                white+=compute_region(integral_image,(self.topLeft[0],int(self.topLeft[1]+2*self.height/3)),self.bottomRight)
            elif(self.type==HaarFeaturesType.four):
                white=compute_region(integral_image,self.topLeft,(int(self.topLeft[0]+self.width/2),int(self.topLeft[1]+self.height/2)))
                black=compute_region(integral_image,(int(self.topLeft[0]+self.width/2),self.topLeft[1]),(self.bottomRight[0],int(self.topLeft[1]+self.height/2)))
                black+=compute_region(integral_image,(self.topLeft[0],int(self.topLeft[1]+self.height/2)),(int(self.topLeft[0]+self.width/2),self.bottomRight[1]))
                white+=compute_region(integral_image,(int(self.topLeft[0]+self.width/2),int(self.topLeft[1] + self.height / 2), self.bottomRight))
                
                
            return (white-black)   
        
        
        
        def vote(self,integral_image):
            feature_score=self.calc_score(integral_image)
            if(feature_score< self.parity*self.threshold):
                return self.weight *1;
            else:
                return 0;
            
                

In [71]:
#face_detect=cv.CascadeClassifier('haarcascade_frontalface_alt.xml')

Real time video

In [22]:
cap=cv.VideoCapture(0)
while(True):
    #read Frames
    ret,frame=cap.read()
    #convert frame to gray scale 
    gray=cv.cvtColor(frame,cv.COLOR_BGR2GRAY)
    
    #integral image
    
    
   # faces=face_detect.detectMultiScale(gray,1.1,4)
    #for(x,y,w,h)in faces:
     #cv.rectangle(frame,(x,y),(x+w,y+h),(255,0,0),3)
    cv.imshow('fram', gray)
    #exit
    if cv.waitKey(1)& 0xFF==ord('q'):
        break
        
cap.realse()
cv.destoryAllWindows()
        
        
        

AttributeError: 'cv2.VideoCapture' object has no attribute 'realse'

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

...

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b

Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed by the remote host
Exception in callback BaseSelectorEventLoop._read_from_self()
handle: <Handle BaseSelectorEventLoop._read_from_self()>
Traceback (most recent call last):
  File "C:\Users\esraa\anaconda3\lib\asyncio\events.py", line 81, in _run
    self._context.run(self._callback, *self._args)
  File "C:\Users\esraa\anaconda3\lib\asyncio\selector_events.py", line 120, in _read_from_self
    data = self._ssock.recv(4096)
ConnectionResetError: [WinError 10054] An existing connection was forcibly closed b